In [128]:
#### specify path of Julia Code for 2D Models ####
### By default the working directory ./2D_Models ###
path = string( pwd(), "/2D_Models/")

"/home/jakob/Dokumente/Repositories/Modeling_Framework/2D_Models/"

In [129]:
##### include 2D Modelling Framework ####
include(string(path, "./2D_model_library.jl"));


########## OPERATIONAL ##########
##### how to chose the actual velocity? #####

#op_model = "Constant"
#op_model = "Collision_Free_Speed"
#op_model = "RVO"
#op_model = "SocialForce"
#op_model = "AV_Model"
#op_model = "AV_IN_Model"
#op_model = "PowerLaw"
#op_model = "IN_Costfunction"
#op_model = "IN_Model"
#op_model = "SocialForce"
#op_model = "SocialForce_Elliptical_A"
#op_model = "SocialForce_Elliptical_B"
op_model = "SocialForce_CollisionPrediction"


include_op_model(op_model, path)

########## TACTICAL ##########
#### how to chose the preferred velocity? ###

tact_model = "Constant"
#tact_model = "IN_Model"

include_tact_model(tact_model, path)


########## STRATEGIC ##########
### how to chose the desired velocity ###

strat_model = "Constant"
#strat_model = "Towards_Goal"
#strat_model = "Two_Goals"

include_strat_model(strat_model, path)


########## OPTIMIZATION SCHEME ##########
### If optimization of a cost-function is included, how to solve? ###

#optimization_scheme = "Regular_Sampling"
optimization_scheme = "Random_Sampling"

include_optimization_scheme(optimization_scheme, path)


##### which update scheme? #####

update = "Parallel_Update"
#update = "Step_Update"

include_update(update, path)


##### which order? i.e. Acceleration or Velocity based? ####
#order = "first"
order = "second"

include_order(order, path)


##### PERCEPTIONAL MODEL ####
perception_model = "None"
#perception_model = "Only_in_Front"

include_perception_model(perception_model, path)

The following parameters were given in zanlungo_SocialForceModel_2011:
[2.0, 1.7, 0.0, 0.0, 0.0, 0.0, 0.0, 0.66, 1.71, 0.0, 0.0, 0.0, 0.71, 0.0]
v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ


In [151]:
#### parameters of the agents ####
p = [2.0, 0.0, 0.0, 0.0, 0.3, 0.0, 0.0, 0.66, 1.71, 0.0, 0.0, 0.0, 0.71, 0.0]
# ModelParameter: v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ
p_desc = "v_max, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ"

### of the system ###
ρ = 2.55#3.74

system_size = (5.0, 5.0) #important for periodic boundaries
L = 5
N = Int(round(ρ*L*L))

### of the simulation ###
sim_p = [0.0, 10.0, 0.05, 0.01, 3.0] #t_relax, t_max, dt_save, dt, r
sim_p_desc = "t_relax, t_max, dt_save, dt, r"

### initialize geometry ###
geometrie = create_geometry_single_obstacle((37.5,31.5), 0.3)

### initialize crowd ###
menge = create_crowd(N, geometrie)
Init_Hom_Parameters!(p, menge)
Init_Hom_Vels!(menge, 0.1)
Init_E_des!(menge, (1.0, 0.0))
Init_Random_Headings!(menge)
CrowdOneSide!(menge, 0.4, 0.0, L)

In [152]:
positions, headings = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);

In [153]:
using GR
GR.inline("mov")

j = 1

dt_save = sim_p[3]
geometry_x, geometry_y = rewrite_geometry(geometrie)
boundaries_x, boundaries_y = boundaries_rectangle_positions(system_size)

while j*sim_p[3] < sim_p[2]-sim_p[1]
    
        GR.clearws()

        GR.setwindow(-1, 11, -1, 11)
        GR.setviewport(0.0, 1, 0.0, 1)    

        plot_boundaries(boundaries_x, boundaries_y, 0.2, 999)        

        plot_agents(positions[j, :], headings[j, :], 2.3, 100, 0.7, 999, 0.1)
    
        model = op_model
        timer = string("time ", round(j*dt_save, digits = 1), "s")
        GR.text(0.7, 0.95, timer)
        GR.text(0.7, 0.9, model)
        
        GR.updatews()
    
        j = j+1
end

In [154]:
GR.show()

GR.HTML("<video autoplay controls><source type=\"video/mp4\" src=\"data:video/mp4;base64,AAAAFGZ0eXBxdCAgAAACAHF0ICAAAAAId2lkZQAxdHZtZGF0AAACsQYF//+t3EXpvebZSLeWLNgg2SPu73gyNjQgLSBjb3JlIDE2MyAtIEguMjY0L01QRUctNCBBVkMgY29kZWMgLSBDb3B5bGVmdCAyMDAzLTIwMjEgLSBodHRwOi8vd3d3LnZpZGVvbGFuLm9yZy94MjY0Lmh0bWwgLSBvcHRpb25zOiBjYWJhYz0xIHJlZj0zIGRlYmxvY2s9MTowOjAgYW5hbHlzZT0weDM6MHgxMTMgbWU9aGV4IHN1Ym1lPTcgcHN5PTEgcHN5X3JkPTEuMDA6MC4wMCBtaXhlZF9yZWY9MSBtZV9yYW5nZT0xNiBjaHJvbWFfbWU9MSB0cmVsbGlzPTEgOHg4ZGN0PTEgY3FtPTAgZGVhZHpvbmU9MjEsMTEgZmFzdF9wc2tpcD0xIGNocm9tYV9xcF9vZmZzZXQ9LTIgdGhyZWFkcz0xMiBsb29rYWhlYWRfdGhyZWFkcz0yIHNsaWNlZF90aHJlYWRzPTAgbnI9MCBkZWNpbWF0ZT0xIGludGVybGFjZWQ9MCBibHVyYXlfY29tcGF0PTAgY29uc3RyYWluZWRfaW50cmE9MCBiZnJhbWVzPTMgYl9weXJhbWlkPTIgYl9hZGFwdD0xIGJfYmlhcz0wIGRpcmVjdD0xIHdlaWdodGI9MSBvcGVuX2dvcD0wIHdlaWdodHA9MiBrZXlpbnQ9MjUwIGtleWludF9taW49MjQgc2NlbmVjdXQ9NDAgaW50cmFfcmVmcmVzaD0wIHJjX2xvb2thaGVhZD00MCByYz1hYnIgbWJ0cmVlPTEgYml0cmF0ZT00MDAwIHJhdGV0b2w9MS4wIHFjb21wPTAuNjAgcXBtaW49MCBxcG1heD02OSBxcHN0ZXA9NCBpcF9yYXRpbz0xLjQwIGFxPTE6MS4wMACAAABg/2WIhAAa//731LfMsu1Tb7YLqPeiniZfQ3UlAZuWxO06gAAAAwAAAwAAAwDpVIJjfO4A0Yy0AAGmi/SZxwabwAHQGDGM77Gdn2nqvAAWvZ6FoOJ+m2zddvNGY1PNZxqSA/qFRZmVjZ76nsQkA36vZ1t90oJ7I5RD2VckVMfyHmVJdrl7Q6j0N37upVso8tOotrXFVTjVGkhhoXrdZHzshRDEePDLsoPQjxXXWdPdzOhTyL0NMFdep/kRldWxURL+4zu5YHAGRsBRQOfxkgwNt2cZ/Q8WW5KWwTOAAwkeRIsc/4qZZiyzARb2d7Dcj2Abc6I03wQ9K20p1mJ0tpttY3GecW1+pahjzbhE60xtX/7oWToJUJPpqnUQS9VJMcEm3MrtcS95kjduVGYe3cBjsQ7muzjdxvyWTP0qeSY5cODrNsmXb85rPfYBi1qrP8SGvDYBhnt679EvrOJ2ldPdYo2kLXa/Afa8X8n3X0sl4ckDoXDM8tyxBuqTCR8EcKTjGUMZpXEpkPJ5RJ/V1Oh/mxMrEB3wsiXzlpmChXFtG3hzIcydZtGJE26p4/////42sUJlo2xGuiCjhFiTK+luztOld9Qc/jpud47dZNQJRTpOxYB4XTGcA+w0ZSfH+sajowD05ecqF0sY4YXz6sMzVXmvR96OQVvOEIAcExeL6+37+9WOTu+neRCr0s5MVO6CN8WpnZR1ZqT4Dqwp4LBvO9c5HTWyz6n3y1fpPxPKDl54s4P/I2x3g6qV9xmLELUAQqro6nBV706LIk6OfunvsFTnfE6mQGH72Rf7xiGXfWP7yoQzTCmpKZSUcBcUGsYo7vZSjYAyr0AVr5vB7AHT9/6SXmqR/m0U5ni3I0GgF5ZF6JaqGHp261SY08qVf/ygp0LdMBPZR5DnDUVj4gXhTapFizvLPCrukBlZPCD16WcpOkGB/oxY9YXT5+gErvwwmtneBNMTtydFW0YuoAbSTguTbVp2ghWrO5a5yL1jShsy5Qlo+uInOflOlZyeI/jNuuBG+OcmzOMk1I+pNXJgwDOmoTllFSpkItpAAhsVF/vv2YR/tfgZDvVqXKfxTat3QAB4G0MKdNXEj3zeVNoiFR5nIE1+vY3spL3hAa1JeaFoq6GwqXaZYkFQq+xdZLrsnTEVNf4xwe78zjc+4zQzmkIxIqhsax3atjxmistcmm0a/7XFxMb+PNLSK3NkDYyvS8ykZ3xewoS5owNSpxEz9jRM1vMNg2IwW8pWL0qOJTdITUZwK7T39/Sy3Lk4qFt7cFkUeINLdA0Fnxv3+KMoTjwpYVxCVGqXo1XUNQcan3i0Gd/pCdjeVYEzQuUiaw/EbozlC5fAePIzzqkuYztkuVdTKzds2Dy5qIcorEehTXFE2a9i3RMhmxmAE7RV7tTJfS+HjFDAjeKhVt+7h51yabBbYwli3pMgVnwcuWs6IIRTEb6BpSm+eMFwd+u0GLYWkK5RMWQ3G3H3H4pmhEDew+5HZD/zHRyQ7NBjmgJyTw/uq202BqpYTBdkZKMJIwwujxghYXXsReKjL4j2pf/rnv7O4P7zPiyOMx8nGbhScM3ukQgQsG1L3KWsu8nM6qqN5ky78q3LPYiDzfxYDu7lYZVUQPbQYXF4eA3gpSxkwZ0hen5gCMtdQQuli3zv6IV5+JjT93OIeF2mFUt4Bm9bmnc8E3Qazbk+7HhbSmWCRPn1+PftuQhGxadkRPHSmOM2X04fqyxxugmDt8J36ueJa8rwOBxmn1HXdK8h/7UmzeBQMK+YE7ZvPzmGYSc3Sjh06nffCQrWIFAPBuAy1Okc346WJYMAdKbsuSoTunKChWMwbsK5Xe9koBI1t1aGg68/LhKqfqKDuRCfqt0vKQ+2U2K+amsbrCyOYVB5gdF0K0leG+iJrcDaonGkwMmwK+rG0KGcyM72UZvRt3rzAFO1rjQTM+Rcf0cwdX2nHRtDEhb2eALlrV7DQHdfVQ+FYU/27uyU63V9prJk2IB1evxEkZhY9s3OvwAokn+RwmN9JMWZzytnXZIuZ8m0Bf7gQ6HoQhhyR6pmqVZo+cE1qBz8pMZ4XTL6VxsqlnyyEvfrurT1bMepnknLeq/JiF/qV9Wh+/v5HB+P3f/2wUJQrmZrGV3P1YW9t9fZU9RM9thbVOi/+zN2il/IzkWxrUGQ7KsWGDyV/1RvY5hGQIHMgNjbCGBLYmLSJPoJunZHddokkBNUKP++bxuZ/WVAK/BjAQ/N88NnKaCA6VySe3/OC2dum9gbC9/oUfMSGGUfZVCQunSaV5h4TDqFrJsE+SIu6+YKsnb207GttdKIl+6HjkrV07tm057QPRPqcXZv4mohgl6UvRJbafb3puza/8p3+03kEgJSY0eyfLV3L84Lq3XL8gv/9B7zjXbIpp3GBbDM1PKR6tdwFuuWs1tiI/Do57RcSNZYyPjN6tXLbQd8j12bbjrY2EEK03dPS6OMjMAgfnQ51ny54IvrrFEhvQy3G+uXWjn5pI190e9HljsGZbarbYXPIvcWaHEruEwGo4qywTjMr11eTQ2lE+VhWQ3N9eennr2+wyVfLR9QSk7AOccjiBX5Nur1o355EtkEeOTTsmtlEfCII1MuOLttr1KPB0yOwgKlQXrQwYOQtIy4Gp+AivZj6xVE+WFlfgYVUikt5Kc/DOcEFnV7bKVcGmG+Kq+RlLEJ91982fPwjT7qLLf1OgiyNxPyAJsNPzhJKs5DzqZbbfplBXq8I1K+vp+NkxcPw0/ISZS12T2WkgvxHUn/+szU5+cPgWmhGXDzAnvJ/cWmMe7mkSzcl43qW7BUHrfQwWO2ZT6355Dt/gPMVF1Mc97C4IjoKy9/vw7hzvTjS/pUCKd+O/NTV/P7Z0SpojnLSVYQRTZYEBQpzWduaiTzPRyhiDgHd0Ctl1JCvwixhst0virdUxf/vbW

In [23]:
Path = "/home/jakob/Dokumente/Sim_Data/"
dir = "Waiting_AV"
header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size);

Save_Data!(Path, dir, header, positions)

In [ ]:
name = "Waiting"
path = "/home/jakob/Dokumente/Renne_Software/UMANS_3/examples/agents/"

#Set_Goal_from_E_des!(menge, (99.0, 0.0))
Change_Coordinate_System_Agents!(menge, -1 .*(system_size./2))
Write_Agents_XML(menge, name, path)

In [ ]:
path = "/home/jakob/Dokumente/Renne_Software/WithWaiting/examples/"
policy = "Moussaid"
agents = "Waiting_"

name = string(agents, policy)


Write_Scenario_XML(path, name, sim_p, system_size, policy, agents)